In [179]:
import os
import glob
import pickle
import pandas as pd
import numpy as np

from dask.diagnostics import ProgressBar

from arboreto.utils import load_tf_names
from arboreto.algo import grnboost2

from ctxcore.rnkdb import FeatherRankingDatabase as RankingDatabase
from pyscenic.utils import modules_from_adjacencies, load_motifs
from pyscenic.prune import prune2df, df2regulons
from pyscenic.aucell import aucell

import seaborn as sns


In [180]:
import matplotlib.pyplot as plt

In [181]:
import pickle as pkl

In [182]:
def size2(a,b):
    plt.rcParams['figure.figsize'] = (a,b)
def size(a,b):
    plt.gcf().set_size_inches(a,b)

def pklrd(filename):
    with open(filename, "rb") as file:
        data = pkl.load(file)
        return data

def pklwr(data, filename):
    with open(filename, "wb") as file:
        pkl.dump(data, file)

def save(name):
    scjp.save_fig(version,'Fig4_'+name,fig_folder='./Fig4')


plt.rcParams['figure.dpi'] = 300

In [183]:
## tf gene list from http://humantfs.ccbr.utoronto.ca/download.php
## ranking DB, motif from ## https://resources.aertslab.org/cistarget/


In [184]:
import anndata as ad

In [185]:
canrawt = ad.read_h5ad('/home/srkim/write/PCI01.v43.canrawt_final_02.h5ad')

In [186]:
auc_mtx = pd.read_csv('~/pyscenic_canrawt_filtered_mtx.csv', index_col=0)

In [187]:
from pyscenic.rss import regulon_specificity_scores
from pyscenic.plotting import plot_rss
import matplotlib.pyplot as plt
from adjustText import adjust_text
import seaborn as sns
from pyscenic.binarization import binarize

In [188]:
auc_mtx

AR(+)   ATF3(+)  BACH1(+)   BCL6(+)  \
Cell                                                                     
GEX_45_MM_AAACGGGAGACAAGCC-1-0  0.309603  0.009364  0.002260  0.023236   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0  0.161941  0.012431  0.007412  0.044666   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0  0.082826  0.005493  0.001116  0.003092   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0  0.084580  0.007247  0.003033  0.008250   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0  0.040529  0.013412  0.010617  0.052777   
...                                  ...       ...       ...       ...   
5_GEX_9_TTTGTCAAGAGAACAG-1-1    0.000000  0.008593  0.022215  0.066068   
5_GEX_9_TTTGTCAAGATCTGCT-1-1    0.000000  0.013548  0.024009  0.011098   
5_GEX_9_TTTGTCAAGCGTAATA-1-1    0.000000  0.011238  0.029036  0.086111   
5_GEX_9_TTTGTCACAGCTTAAC-1-1    0.089858  0.009337  0.012473  0.089268   
5_GEX_9_TTTGTCACAGGTCCAC-1-1    0.000000  0.014738  0.014347  0.013610   

                                BHLHE40(+)  CREB3L1(+)  CREB3L4(+)  CREB5(+)  \
Cell                                                                           
GEX_45_MM_AAACGGGAGACAAGCC-1-0    0.000000    0.000000    0.011862  0.055846   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0    0.000000    0.000000    0.014205  0.028575   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0    0.000000    0.000000    0.006374  0.050414   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0    0.005695    0.007685    0.006111  0.066095   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0    0.006005    0.005609    0.015350  0.007385   
...                                    ...         ...         ...       ...   
5_GEX_9_TTTGTCAAGAGAACAG-1-1      0.014404    0.000000    0.006128  0.023016   
5_GEX_9_TTTGTCAAGATCTGCT-1-1      0.024810    0.022153    0.048144  0.010927   
5_GEX_9_TTTGTCAAGCGTAATA-1-1      0.021217    0.002209    0.004596  0.019867   
5_GEX_9_TTTGTCACAGCTTAAC-1-1      0.000000    0.001256    0.020073  0.013874   
5_GEX_9_TTTGTCACAGGTCCAC-1-1      0.012568    0.155012    0.363638  0.004549   

                                DDIT3(+)   EGR1(+)  ...  SNAI1(+)   SOX4(+)  \
Cell                                                ...                       
GEX_45_MM_AAACGGGAGACAAGCC-1-0  0.008006  0.007603  ...       0.0  0.015603   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0  0.036296  0.006231  ...       0.0  0.010182   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0  0.002388  0.000000  ...       0.0  0.000104   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0  0.032299  0.000000  ...       0.0  0.000589   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0  0.017359  0.008721  ...       0.0  0.014779   
...                                  ...       ...  ...       ...       ...   
5_GEX_9_TTTGTCAAGAGAACAG-1-1    0.013067  0.008535  ...       0.0  0.006451   
5_GEX_9_TTTGTCAAGATCTGCT-1-1    0.006832  0.006156  ...       0.0  0.004127   
5_GEX_9_TTTGTCAAGCGTAATA-1-1    0.014171  0.001121  ...       0.0  0.015314   
5_GEX_9_TTTGTCACAGCTTAAC-1-1    0.005823  0.021911  ...       0.0  0.011447   
5_GEX_9_TTTGTCACAGGTCCAC-1-1    0.007231  0.000000  ...       0.0  0.000631   

                                 SOX5(+)   SOX6(+)  SPDEF(+)  STAT2(+)  \
Cell                                                                     
GEX_45_MM_AAACGGGAGACAAGCC-1-0  0.000000  0.101619  0.000000  0.015038   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0  0.000000  0.037978  0.000000  0.051826   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0  0.000000  0.025342  0.000000  0.001374   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0  0.000000  0.035098  0.000000  0.001811   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0  0.000000  0.028453  0.000000  0.065320   
...                                  ...       ...       ...       ...   
5_GEX_9_TTTGTCAAGAGAACAG-1-1    0.005515  0.027117  0.000000  0.050422   
5_GEX_9_TTTGTCAAGATCTGCT-1-1    0.014181  0.046673  0.078274  0.009050   
5_GEX_9_TTTGTCAAGCGTAATA-1-1    0.016151  0.000000  0.007810  0.100397   
5_GEX_9_TTTGTCACAGCTTAAC-1-1    0.055287  0.000000  0.000000  0.040609   
5_GEX_9_TTTGTCACAGGTCCAC-1-1    0.114996  0.000000  0.354062  0.026340   

                                 TCF4(+)

In [189]:
cellAnnot = pd.DataFrame(index=auc_mtx.index)

In [190]:
cellAnnot= cellAnnot.merge(canrawt.obs[['anno_final']], left_index=True, right_index=True, how='left')

In [191]:
cellAnnot['Celltype_Garnett'] = cellAnnot['anno_final'].copy()

In [192]:
rss_cellType = regulon_specificity_scores( auc_mtx, cellAnnot['Celltype_Garnett'] )
rss_cellType

AR(+)   ATF3(+)  BACH1(+)   BCL6(+)  BHLHE40(+)  CREB3L1(+)  \
Ep_FXYD2   0.388965  0.225306  0.190530  0.200628    0.177613    0.180385   
Ep_PIFO    0.195639  0.211185  0.217519  0.251494    0.209326    0.177941   
Ep_VGLL1   0.260881  0.306768  0.359137  0.315239    0.316010    0.235239   
Ep_TRIM54  0.296020  0.341267  0.328930  0.273868    0.319524    0.420222   
Ep_KRT6A   0.233046  0.264136  0.297714  0.356530    0.312752    0.189239   
Ep_ZBED6   0.214634  0.223485  0.274827  0.253735    0.242114    0.201480   
Ep_Base    0.218260  0.330624  0.360586  0.377071    0.370101    0.256636   
Ep_MSMB    0.213372  0.356227  0.231506  0.216466    0.229168    0.467505   

           CREB3L4(+)  CREB5(+)  DDIT3(+)   EGR1(+)  ...  SNAI1(+)   SOX4(+)  \
Ep_FXYD2     0.184671  0.301325  0.206436  0.200666  ...  0.171640  0.195748   
Ep_PIFO      0.182825  0.201914  0.196327  0.209717  ...  0.175180  0.196737   
Ep_VGLL1     0.223727  0.300136  0.333696  0.335576  ...  0.235361  0.402097   
Ep_TRIM54    0.277714  0.382003  0.376023  0.300165  ...  0.308438  0.331628   
Ep_KRT6A     0.218941  0.271644  0.274587  0.267085  ...  0.190476  0.275087   
Ep_ZBED6     0.185965  0.246434  0.229304  0.236999  ...  0.200658  0.240373   
Ep_Base      0.244028  0.295801  0.327750  0.342512  ...  0.214682  0.350988   
Ep_MSMB      0.593784  0.269832  0.254894  0.267536  ...  0.177152  0.209871   

            SOX5(+)   SOX6(+)  SPDEF(+)  STAT2(+)   TCF4(+)   TP63(+)  \
Ep_FXYD2   0.180485  0.259947  0.172367  0.188897  0.197513  0.195325   
Ep_PIFO    0.186984  0.208077  0.177509  0.268071  0.202869  0.287377   
Ep_VGLL1   0.216193  0.292679  0.205202  0.323815  0.284225  0.334517   
Ep_TRIM54  0.428012  0.385147  0.309644  0.301728  0.306471  0.323565   
Ep_KRT6A   0.206127  0.252084  0.180924  0.354526  0.352670  0.324958   
Ep_ZBED6   0.231863  0.274186  0.185829  0.237641  0.236060  0.230181   
Ep_Base    0.283101  0.264846  0.231292  0.364289  0.315366  0.312445   
Ep_MSMB    0.216024  0.239657  0.527115  0.219133  0.194410  0.220586   

            ZEB1(+)  ZNF233(+)  
Ep_FXYD2   0.173127   0.201322  
Ep_PIFO    0.192865   0.180070  
Ep_VGLL1   0.257349   0.256051  
Ep_TRIM54  0.239445   0.364688  
Ep_KRT6A   0.417147   0.201637  
Ep_ZBED6   0.212336   0.250250  
Ep_Base    0.290148   0.209854  
Ep_MSMB    0.179029   0.204828  

[8 rows x 72 columns]

In [193]:
rss_cellType = rss_cellType.drop('Ep_Base')

In [194]:
csdict = pklrd('csdict.pkl')

In [195]:
from scipy.stats import ttest_ind

In [196]:
df = auc_mtx.merge(canrawt.obs[['anno_final']], left_index=True, right_index=True).copy()

In [197]:
pvalmtx = pd.DataFrame(columns = rss_cellType.columns, index=rss_cellType.index)

In [198]:
statmtx = pd.DataFrame(columns = rss_cellType.columns, index=rss_cellType.index)

In [199]:
for anno in rss_cellType.index:
    for x in rss_cellType.columns:
        pvalmtx.loc[anno,x] = ttest_ind(df[df['anno_final'] ==anno][x], df[df['anno_final']!=anno][x])[1]
        statmtx.loc[anno,x] = ttest_ind(df[df['anno_final'] ==anno][x], df[df['anno_final']!=anno][x])[0]

In [200]:
ttest_ind(df[df['anno_final'] ==anno][x], df[df['anno_final']!=anno][x])[1]

6.593736703754367e-18

In [201]:
statmtx

AR(+)    ATF3(+)   BACH1(+)    BCL6(+) BHLHE40(+) CREB3L1(+)  \
Ep_FXYD2   73.853036   1.114975   -19.8115 -12.500436 -18.528362  -13.61192   
Ep_PIFO    -5.973529 -13.125871 -10.675191  10.766147  -9.645161 -16.837975   
Ep_VGLL1    1.223111   1.589377  31.992238   4.654621   7.614291 -18.898784   
Ep_TRIM54   0.792764 -10.205617 -19.503834 -38.992299 -10.849221  22.848613   
Ep_KRT6A   -9.513275 -25.167148 -10.237718  22.731625   3.983484 -31.989678   
Ep_ZBED6   -1.922975  -8.766018  25.949357   9.602631   3.495961 -11.682484   
Ep_MSMB    -9.035171  46.538366 -25.669135 -29.002904  -16.36931   95.88062   

           CREB3L4(+)   CREB5(+)   DDIT3(+)    EGR1(+)  ...   SNAI1(+)  \
Ep_FXYD2    -8.098529  69.319647  -7.907638  -7.948865  ...  -6.027041   
Ep_PIFO    -10.019894 -17.666724  -16.36806   -7.99298  ...  -6.169635   
Ep_VGLL1   -14.485431  -2.445519  15.268415  19.710925  ...   3.372175   
Ep_TRIM54   -14.41601   9.643804   8.562352 -13.747384  ...  19.557156   
Ep_KRT6A   -16.150391  -19.95731 -10.682488 -12.719774  ...   -9.19882   
Ep_ZBED6   -10.295551   4.653797  -3.613779   2.116372  ...  -0.685113   
Ep_MSMB    164.092813  -5.829087 -10.142274  -0.368031  ...  -9.099258   

             SOX4(+)    SOX5(+)    SOX6(+)   SPDEF(+)   STAT2(+)    TCF4(+)  \
Ep_FXYD2  -12.680978  -8.848136  22.390709 -10.081475 -20.267605  -7.387333   
Ep_PIFO   -16.978053  -9.229117  -9.328968 -10.591779  22.827962  -8.358187   
Ep_VGLL1   51.294881 -13.379646  -0.762432 -14.665357   9.528974   0.487247   
Ep_TRIM54  -11.72822  34.952035  19.040871  -1.370008 -29.360534  -4.345886   
Ep_KRT6A  -12.441589 -16.698839 -17.989251 -20.632504  21.824079  19.293779   
Ep_ZBED6    1.937398   4.411287  20.628104  -9.669867  -0.668157   2.845847   
Ep_MSMB   -27.501054  -9.639122 -12.473322  104.39429 -31.995369 -21.927712   

             TP63(+)    ZEB1(+)  ZNF233(+)  
Ep_FXYD2  -11.980214 -10.554624  -2.378117  
Ep_PIFO    28.731994  -7.449483  -8.826533  
Ep_VGLL1   19.126396  -4.556643   1.489811  
Ep_TRIM54 -12.582282 -17.764333  27.725785  
Ep_KRT6A     6.73512  48.859822 -13.954431  
Ep_ZBED6   -3.020064   -2.50314   9.234646  
Ep_MSMB   -22.339022 -17.736027  -8.636614  

[7 rows x 72 columns]

In [203]:
statmtx.T.sort_values('Ep_FXYD2', ascending=False).head(10)

Ep_FXYD2    Ep_PIFO   Ep_VGLL1  Ep_TRIM54   Ep_KRT6A   Ep_ZBED6  \
NR5A2(+)  111.005016 -10.578198 -14.321429   6.871851 -17.327948  -4.498371   
PBX3(+)    81.003605 -10.114844  -12.64767 -11.671898    3.50761  -5.721162   
AR(+)      73.853036  -5.973529   1.223111   0.792764  -9.513275  -1.922975   
JUN(+)     70.060493 -18.872157   1.982148   5.092525 -33.114898  -1.511761   
CREB5(+)   69.319647 -17.666724  -2.445519   9.643804  -19.95731   4.653797   
FOSB(+)    42.257186 -16.572385  -4.383368   4.180887 -27.339143   0.653572   
JUNB(+)    30.789576  -4.829299 -18.573872 -20.200318  13.815355  -7.117866   
HNF1B(+)   24.206903 -18.874111  -15.69572  63.360471 -34.898897   8.418233   
MEIS2(+)   22.870567    -9.9129  -2.513198  31.750365 -25.766512   3.737336   
SOX6(+)    22.390709  -9.328968  -0.762432  19.040871 -17.989251  20.628104   

            Ep_MSMB  
NR5A2(+)  -0.594094  
PBX3(+)    4.825338  
AR(+)     -9.035171  
JUN(+)      8.67822  
CREB5(+)  -5.829087  
FOSB(+)   10.954352  
JUNB(+)  -13.014554  
HNF1B(+)  -5.648267  
MEIS2(+) -14.256965  
SOX6(+)  -12.473322

In [204]:
def plot_rss(rss, cell_type, csdict, top_n=5, max_n=None, ax=None):
    if ax is None:
        _, ax = plt.subplots(1, 1, figsize=(4, 4))
    if max_n is None:
        max_n = rss.shape[1]
    data = rss.T[cell_type].sort_values(ascending=False)[0:max_n]
    ax.plot(np.arange(len(data)), data, '.', color='lightgrey')
    ax.set_ylim([floor(data.min() * 100.0) / 100.0, ceil(data.max() * 100.0) / 100.0])
    ax.set_ylabel('RSS')
    ax.set_xlabel('Regulon')
    ax.set_title(cell_type)
    ax.set_xticklabels([])

    font = {
        'color': csdict[cell_type],
        'weight': 'normal',
        'size': 4,
    }

    for idx, (regulon_name, rss_val) in enumerate(zip(data[0:top_n].index, data[0:top_n].values)):
        ax.plot([idx, idx], [rss_val, rss_val], '.', c=csdict[cell_type])
        ax.text(
            idx + (max_n / 25),
            rss_val,
            regulon_name,
            fontdict=font,
            horizontalalignment='left',
            verticalalignment='center',
        )

In [205]:
from math import ceil, floor

In [206]:
ndict = {}

In [207]:
for anno in statmtx.index:
    print(anno, list(statmtx.T[statmtx.T[anno] > 50].index))
    ndict[anno] = len(list(statmtx.T[statmtx.T[anno] > 50].index))

Ep_FXYD2 ['AR(+)', 'CREB5(+)', 'JUN(+)', 'NR5A2(+)', 'PBX3(+)']
Ep_PIFO ['FOXJ1(+)', 'RFX3(+)']
Ep_VGLL1 ['SOX4(+)']
Ep_TRIM54 ['HNF1B(+)', 'HOXB5(+)', 'HOXB6(+)', 'HOXB7(+)', 'HOXC10(+)', 'ONECUT2(+)']
Ep_KRT6A ['KLF8(+)', 'MAF(+)']
Ep_ZBED6 []
Ep_MSMB ['CREB3L1(+)', 'CREB3L4(+)', 'EGR2(+)', 'FOXA3(+)', 'SPDEF(+)']


In [210]:
for anno in statmtx.index:
    ndict[anno] = 5

In [231]:
cats = sorted(list(set(rss_cellType.index)))
cats = 'Ep_FXYD2,Ep_MSMB,Ep_TRIM54,Ep_VGLL1,Ep_PIFO,Ep_KRT6A'.split(",")


fig = plt.figure(figsize=(6,6))
for c,num in zip(cats, range(1,len(cats)+1)):
    x=rss_cellType.T[c]
    ax = fig.add_subplot(2,3,num)
    plot_rss(rss_cellType, c, csdict,max_n=None, top_n=ndict[c], ax=ax)
    ##ax.set_ylim( x.min()-(x.max()-x.min())*0.05 , x.max()+(x.max()-x.min())*0.05)
    ax.set_ylim(0,0.7)
    for t in ax.texts:
        t.set_fontsize(9)
        t.set_c(csdict[c])
    ax.set_ylabel('')
    ax.set_xlabel('')
    ax.set_xticks([])
    ax.set_title(c, color=csdict[c])
    adjust_text(ax.texts, autoalign='xy', ha='right', va='bottom', arrowprops=dict(arrowstyle='-',color='lightgrey', lw=0.3), precision=0.001)
 
fig.text(0.5, 0.0, 'Regulon', ha='center', va='center', size='x-large')
fig.text(0.00, 0.5, 'Regulon specificity score (RSS)', ha='center', va='center', rotation='vertical', size='x-large')
plt.tight_layout()
plt.rcParams.update({
    'figure.autolayout': True,
        'figure.titlesize': 'large' ,
        'axes.labelsize': 'medium',
        'axes.titlesize':'large',
        'xtick.labelsize':'medium',
        'ytick.labelsize':'medium'
        })

plt.savefig('/home/srkim/02_PancCa/16_FIGURE/Fig4/specific.pdf', bbox_inches='tight', dpi=300)

In [25]:
binary_mtx, auc_thresholds = binarize( auc_mtx, num_workers=25 )
binary_mtx.head()

AR(+)  ATF3(+)  BACH1(+)  BCL6(+)  BHLHE40(+)  \
Cell                                                                            
GEX_45_MM_AAACGGGAGACAAGCC-1-0      1        0         0        0           0   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0      1        0         0        0           0   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0      1        0         0        0           0   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0      1        0         0        0           0   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0      0        0         0        1           0   

                                CREB3L1(+)  CREB3L4(+)  CREB5(+)  DDIT3(+)  \
Cell                                                                         
GEX_45_MM_AAACGGGAGACAAGCC-1-0           0           0         0         0   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0           0           0         0         0   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0           0           0         0         0   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0           0           0         0         0   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0           0           0         0         0   

                                EGR1(+)  ...  SNAI1(+)  SOX4(+)  SOX5(+)  \
Cell                                     ...                               
GEX_45_MM_AAACGGGAGACAAGCC-1-0        0  ...         0        0        0   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0        0  ...         0        0        0   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0        0  ...         0        0        0   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0        0  ...         0        0        0   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0        0  ...         0        0        0   

                                SOX6(+)  SPDEF(+)  STAT2(+)  TCF4(+)  TP63(+)  \
Cell                                                                            
GEX_45_MM_AAACGGGAGACAAGCC-1-0        1         0         0        0        0   
GEX_45_MM_AAAGATGAGCTCCTCT-1-0        0         0         0        0        1   
GEX_45_MM_AAAGATGTCGCTAGCG-1-0        0         0         0        0        0   
GEX_45_MM_AAAGCAAAGGCGACAT-1-0        0         0         0        0        0   
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0        0         0         0        0        0   

                                ZEB1(+)  ZNF233(+)  
Cell                                                
GEX_45_MM_AAACGGGAGACAAGCC-1-0        0          0  
GEX_45_MM_AAAGATGAGCTCCTCT-1-0        0          0  
GEX_45_MM_AAAGATGTCGCTAGCG-1-0        0          0  
GEX_45_MM_AAAGCAAAGGCGACAT-1-0        0          0  
GEX_45_MM_AAAGCAAAGGGTCGAT-1-0        1          0  

[5 rows x 72 columns]

In [26]:
r = ['NR5A2(+)','AR(+)','PBX3(+)','RFX3(+)']

fig, axs = plt.subplots(1,4, figsize=(12, 4), dpi=150, sharey=False)
for i,ax in enumerate(axs):
    sns.distplot(auc_mtx[ r[i] ], ax=ax, norm_hist=True, bins=100)
    ax.plot( [ auc_thresholds[ r[i] ] ]*2, ax.get_ylim(), 'r:')
    ax.title.set_text( r[i] )
    ax.set_xlabel('')
    
fig.text(-0.01, 0.5, 'Frequency', ha='center', va='center', rotation='vertical', size='large')
fig.text(0.5, -0.01, 'AUC', ha='center', va='center', rotation='horizontal', size='large')

fig.tight_layout()

/home/srkim/.conda/envs/pyscenic/lib/python3.7/site-packages/seaborn/distributions.py:2619: FutureWarning: `distplot` is a deprecated function and will be removed in a future version. Please adapt your code to use either `displot` (a figure-level function with similar flexibility) or `histplot` (an axes-level function for histograms).
  warnings.warn(msg, FutureWarning)
/home/srkim/.conda/envs/pyscenic/lib/python3.7/site-packages/seaborn/distributions.py:2619: FutureWarning: `distplot` is a deprecated function and will be removed in a future version. Please adapt your code to use either `displot` (a figure-level function with similar flexibility) or `histplot` (an axes-level function for histograms).
  warnings.warn(msg, FutureWarning)
/home/srkim/.conda/envs/pyscenic/lib/python3.7/site-packages/seaborn/distributions.py:2619: FutureWarning: `distplot` is a deprecated function and will be removed in a future version. Please adapt your code to use either `displot` (a figure-level functio